In [1]:
pip install tableauhyperapi pandas

  Using cached tableauhyperapi-0.0.19484-py3-none-win_amd64.whl.metadata (1.3 kB)
  Using cached pandas-2.2.2-cp39-cp39-win_amd64.whl.metadata (19 kB)
  Using cached cffi-1.16.0-cp39-cp39-win_amd64.whl.metadata (1.5 kB)
  Using cached numpy-2.0.0-cp39-cp39-win_amd64.whl.metadata (60 kB)
  Using cached pytz-2024.1-py2.py3-none-any.whl.metadata (22 kB)
  Using cached tzdata-2024.1-py2.py3-none-any.whl.metadata (1.4 kB)
  Using cached pycparser-2.22-py3-none-any.whl.metadata (943 bytes)
Using cached tableauhyperapi-0.0.19484-py3-none-win_amd64.whl (53.8 MB)
Using cached pandas-2.2.2-cp39-cp39-win_amd64.whl (11.6 MB)
Using cached cffi-1.16.0-cp39-cp39-win_amd64.whl (181 kB)
Using cached numpy-2.0.0-cp39-cp39-win_amd64.whl (16.5 MB)
Using cached pytz-2024.1-py2.py3-none-any.whl (505 kB)
Using cached tzdata-2024.1-py2.py3-none-any.whl (345 kB)
Using cached pycparser-2.22-py3-none-any.whl (117 kB)
Note: you may need to restart the kernel to use updated packages.


In [7]:
import zipfile
import os
from tableauhyperapi import HyperProcess, Connection, Telemetry, TableName, Inserter, HyperException
import pandas as pd
import requests

In [8]:
twbx_url = 'https://public.tableau.com/workbooks/MorbilidadHIS_16993000199210.twb'
twbx_file_path = 'Morbilidad HIS.twbx'
extracted_folder = 'folder_extraido'
output_csv_path = 'toymuerto.csv'

In [ ]:
# Descargar el archivo .twbx
response = requests.get(twbx_url)
with open(twbx_file_path, 'wb') as file:
    file.write(response.content)
print(f"Archivo descargado: {twbx_file_path}")

In [9]:
# Descomprimir el archivo .twbx
with zipfile.ZipFile(twbx_file_path, 'r') as zip_ref:
    zip_ref.extractall(extracted_folder)

In [10]:
# Buscar archivos .hyper o .tde dentro de la carpeta extraída
data_file_path = None
for root, dirs, files in os.walk(extracted_folder):
    for file in files:
        if file.endswith('.hyper') or file.endswith('.tde'):
            data_file_path = os.path.join(root, file)
            break

print(data_file_path)

folder_extraido\Data\TableauTemp\TEMP_0g7nmv80bbprba1d3t78d1o5k5mp.hyper


In [6]:
# Conectar al archivo .hyper y listar las tablas
with HyperProcess(telemetry=Telemetry.SEND_USAGE_DATA_TO_TABLEAU) as hyper:
    with Connection(endpoint=hyper.endpoint, database=data_file_path) as connection:
        # Listar las tablas disponibles en el archivo .hyper
        catalog = connection.catalog
        schema_names = catalog.get_schema_names()
        
        for schema in schema_names:
            table_names = catalog.get_table_names(schema=schema)
            print(f"Tablas en el esquema '{schema}': {table_names}")

        # Acceder a la tabla identificada
        table_name = TableName('Extract', 'Extract')  # Usar el esquema y nombre de tabla correctos
        if table_name in table_names:
            query = f"SELECT * FROM {table_name}"

            if limit is not None:
                query += f" LIMIT {limit}"

            # Crear un DataFrame vacío con los nombres de las columnas
            columns = [col.name for col in catalog.get_table_definition(table_name).columns]
            df = pd.DataFrame(columns=columns)
            df_list = []

            try:
                # Iterar sobre las filas del resultado y agregarlas al DataFrame
                with connection.execute_query(query=query) as result:
                    for row in result:
                        row_data = {columns[i]: row[i] for i in range(len(columns))}
                        print(row_data)  # Imprimir cada fila a medida que se obtiene
                        df_list.append(row_data)
            except HyperException as e:
                print(f"Error al ejecutar la consulta: {e}")

            # Convertir la lista de filas a un DataFrame y concatenar
            df = pd.concat([df, pd.DataFrame(df_list)], ignore_index=True)

            # Guardar el DataFrame en un archivo CSV
            df.to_csv(output_csv_path, index=False)
            print(f"Datos guardados en {output_csv_path}")
        else:
            print(f"La tabla '{table_name}' no existe en el archivo .hyper")

Tablas en el esquema '"public"': []
Tablas en el esquema '"Extract"': [TableName('Extract', 'Extract')]
{Name('fec_aten'): Date(2021, 7, 15), Name('ubi_prov'): '1301', Name('etapa'): 1, Name('sexo'): 'F', Name('aten'): 3, Name('Departamento'): 'LA LIBERTAD', Name('Provincia'): 'TRUJILLO', Name('Distrito'): 'SALAVERRY', Name('REGION'): 'COSTA', Name('AREA_Res'): 'RURAL', Name('ALTITUD'): 3, Name('desc_cap'): 'CAPITULO I: CIERTAS ENFERMEDADES INFECCIOSAS Y PARASITARIAS', Name('desc_gru'): '(A00 - A09) ENFERMEDADES INFECCIOSAS INTESTINALES', Name('desc_cat'): 'A07 - OTRAS ENFERMEDADES INTESTINALES DEBIDAS A PROTOZOARIOS', Name('NOMBDEP'): 'LA LIBERTAD', Name('NOMBPROV'): 'TRUJILLO', Name('Geometry'): b'\x07\xaa\x02\x99i\xc1\xb8\x01\x03\n\x14\x13\x03\xa7\x94\xb4\xf1\n\xe7\xf3\xb8\x80g\xb0\xc3\xd1_\xbe\xba\xb3_\x01\xb6_\x9e\x10\xd9\xb3\xa7\x92\n\xa9\xde\xcf\xbcf\xfa\xdf\x08\xf1\xc4)\xf6[\xfd\xb3\x03\x94\x82\x0c\xcf\xcc/\xa2\xee\x13\x83\xa7%\xf6\xbb\x11\xbd\xc1;\xc6\xfa\t\xb3\x89V\x8d\xc7\x0

C:\Users\USUARIO\AppData\Local\Temp\ipykernel_9948\1770468759.py:36: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df = pd.concat([df, pd.DataFrame(df_list)], ignore_index=True)


PermissionError: [Errno 13] Permission denied: 'toymuerto.csv'

In [11]:
# Lista de columnas que queremos conservar
desired_columns = ["fec_aten", "ubi_prov", "etapa", "sexo", "aten", "Departamento", "Provincia", "Distrito", "REGION", "AREA_Res", "ALTITUD", "desc_cap", "desc_gru", "desc_cat", "NOMBDEP", "NOMBPROV"]

# Información extraída del log
num_rows = 2188790  # Número de filas
num_cols = 24  # Número de columnas
result_size_mb = 63124.1  # Tamaño del resultado en MB

# Imprimir información del conjunto de datos
print(f"Cantidad de filas: {num_rows}")
print(f"Cantidad de columnas: {num_cols}")
print(f"Tamaño del resultado: {result_size_mb} MB")



Cantidad de filas: 2188790
Cantidad de columnas: 24
Tamaño del resultado: 63124.1 MB


In [13]:
# Variable para definir el número de filas a descargar
limit = 100  # Cambia esto para definir cuántas filas quieres descargar, o déjalo como None para descargar todas

# Conectar al archivo .hyper y listar las tablas
with HyperProcess(telemetry=Telemetry.SEND_USAGE_DATA_TO_TABLEAU) as hyper:
    with Connection(endpoint=hyper.endpoint, database=data_file_path) as connection:
        # Listar las tablas disponibles en el archivo .hyper
        catalog = connection.catalog
        schema_names = catalog.get_schema_names()
        
        for schema in schema_names:
            table_names = catalog.get_table_names(schema=schema)
            print(f"Tablas en el esquema '{schema}': {table_names}")

        # Acceder a la tabla identificada
        table_name = TableName('Extract', 'Extract')  # Usar el esquema y nombre de tabla correctos
        if table_name in table_names:
            # Construir la consulta con las columnas deseadas
            columns_str = ', '.join(desired_columns)
            query = f"SELECT * FROM {table_name}"
            if limit is not None:
                query += f" LIMIT {limit}"

            # Crear una lista para almacenar las filas
            df_list = []

            try:
                # Iterar sobre las filas del resultado y agregarlas a la lista
                with connection.execute_query(query=query) as result:
                    for row in result:
                        row_data = {desired_columns[i]: row[i] for i in range(len(desired_columns))}
                        df_list.append(row_data)
            except HyperException as e:
                print(f"Error al ejecutar la consulta: {e}")

            # Convertir la lista de filas a un DataFrame
            df = pd.DataFrame(df_list, columns=desired_columns)

            # Guardar el DataFrame en un archivo CSV
            df.to_csv(output_csv_path, index=False)
            print(f"Datos guardados en {output_csv_path}")
        else:
            print(f"La tabla '{table_name}' no existe en el archivo .hyper")

Tablas en el esquema '"public"': []
Tablas en el esquema '"Extract"': [TableName('Extract', 'Extract')]
Datos guardados en toymuerto.csv


In [39]:
# Definir los nombres de las columnas de la tabla
desired_columns = [
    'Departamento', 'Provincia', 'Distrito', 'anio', 'etapa', 'desc_gru', 'cantidad'
]

# Construir la consulta SQL
query = """
SELECT
    "Departamento",
    "Provincia",
    "Distrito",
    EXTRACT(YEAR FROM "fec_aten") AS anio,
    "etapa",
    "desc_gru",
    COUNT(*) AS cantidad
FROM
    "Extract"."Extract"
GROUP BY
    "Departamento",
    "Provincia",
    "Distrito",
    anio,
    "etapa",
    "desc_gru"
ORDER BY
    "Departamento",
    "Provincia",
    "Distrito",
    anio,
    "etapa",
    "desc_gru";
"""

In [33]:
# Definir los nombres de las columnas de la tabla
column_names = [
    'fec_aten', 'ubi_prov', 'etapa', 'sexo', 'aten', 'Departamento', 'Provincia', 'Distrito', 
    'REGION', 'AREA_Res', 'ALTITUD', 'desc_cap', 'desc_gru', 'desc_cat', 'NOMBDEP', 'NOMBPROV', 'Geometry'
]

# Columnas deseadas (excluyendo Geometry)
desired_columns = column_names[:-1]  # Tomar todas las columnas excepto la última (Geometry)

# Definir filtros para la consulta (ajusta estos valores según sea necesario)
year_filter = "2023"
etapa_filter = "1"  # Índice de etapa
limit = 100

# Construir la consulta SQL
query = f"""
SELECT *
FROM "Extract"."Extract" 
WHERE etapa = '{etapa_filter}' 
AND EXTRACT(YEAR FROM fec_aten) = {year_filter}
LIMIT {limit}
"""



In [40]:
# Conectar al archivo .hyper y ejecutar la consulta
with HyperProcess(telemetry=Telemetry.SEND_USAGE_DATA_TO_TABLEAU) as hyper:
    with Connection(endpoint=hyper.endpoint, database=data_file_path) as connection:
        # Listar las tablas disponibles en el archivo .hyper
        catalog = connection.catalog
        schema_names = catalog.get_schema_names()
        
        for schema in schema_names:
            table_names = catalog.get_table_names(schema=schema)
            print(f"Tablas en el esquema '{schema}': {table_names}")

        # Acceder a la tabla identificada
        table_name = TableName('Extract', 'Extract')  # Usar el esquema y nombre de tabla correctos
        if table_name in table_names:
            # Crear una lista para almacenar las filas
            df_list = []

            try:
                # Iterar sobre las filas del resultado y agregarlas a la lista
                with connection.execute_query(query=query) as result:
                    for row in result:
                        row_data = {desired_columns[i]: row[i] for i in range(len(desired_columns))}
                        row_data['cantidad'] = row[-1]  # Agregar la cantidad de casos
                        df_list.append(row_data)
            except HyperException as e:
                print(f"Error al ejecutar la consulta: {e}")

            # Convertir la lista de filas a un DataFrame
            df = pd.DataFrame(df_list, columns=desired_columns + ['cantidad'])

            # Guardar el DataFrame en un archivo CSV
            df.to_csv(output_csv_path, index=False)
            print(f"Datos guardados en {output_csv_path}")
        else:
            print(f"La tabla '{table_name}' no existe en el archivo .hyper")

Tablas en el esquema '"public"': []
Tablas en el esquema '"Extract"': [TableName('Extract', 'Extract')]
Datos guardados en toymuerto.csv
